# Protein-ligand binding

> In this module, we develop tools to get the binding affinity of protein-ligand

## Setup

In [1]:
#| default_exp binding

In [2]:
#| hide
import sys
sys.path.append("/notebooks/tools")
from nbdev.showdoc import *
%matplotlib inline

In [3]:
#| export
from rdkit import Chem
from rdkit.Chem import AllChem
import subprocess
import os
import py3Dmol
import re

In [3]:
!apt install -yq openbabel

Reading package lists...
Building dependency tree...
Reading state information...
The following additional packages will be installed:
  libopenbabel6 libschroedinger-maeparser1
The following NEW packages will be installed:
  libopenbabel6 libschroedinger-maeparser1 openbabel
0 upgraded, 3 newly installed, 0 to remove and 39 not upgraded.
Need to get 3784 kB of archives.
After this operation, 17.9 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu focal/universe amd64 libschroedinger-maeparser1 amd64 1.2.2-1build1 [89.1 kB]
Get:2 http://archive.ubuntu.com/ubuntu focal/universe amd64 libopenbabel6 amd64 3.0.0+dfsg-3ubuntu3 [3568 kB]
Get:3 http://archive.ubuntu.com/ubuntu focal/universe amd64 openbabel amd64 3.0.0+dfsg-3ubuntu3 [127 kB]
Fetched 3784 kB in 0s (16.5 MB/s)

78Selecting previously unselected package libschroedinger-maeparser1:amd64.
(Reading database ... 81360 files and directories currently installed.)
Preparing to unpack .../libschroedinger-

In [4]:
# !wget https://github.com/gnina/gnina/releases/download/v1.0.3/gnina #check the latest version please

In [4]:
!chmod +x gnina

In [5]:
!./gnina

Missing receptor.

Correct usage:

Input:
  -r [ --receptor ] arg            rigid part of the receptor
  --flex arg                       flexible side chains, if any (PDBQT)
  -l [ --ligand ] arg              ligand(s)
  --flexres arg                    flexible side chains specified by comma 
                                   separated list of chain:resid
  --flexdist_ligand arg            Ligand to use for flexdist
  --flexdist arg                   set all side chains within specified 
                                   distance to flexdist_ligand to flexible
  --flex_limit arg                 Hard limit for the number of flexible 
                                   residues
  --flex_max arg                   Retain at at most the closest flex_max 
                                   flexible residues

Search space (required):
  --center_x arg                   X coordinate of the center
  --center_y arg                   Y coordinate of the center
  --center_z arg                

## Get protein and ligand

In [8]:
#nature medicine paper, mrtx
!wget http://files.rcsb.org/download/7T47.pdb

--2023-05-10 18:18:47--  http://files.rcsb.org/download/7T47.pdb
Resolving files.rcsb.org (files.rcsb.org)... 128.6.158.70
Connecting to files.rcsb.org (files.rcsb.org)|128.6.158.70|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/octet-stream]
Saving to: ‘7T47.pdb’

7T47.pdb                [ <=>                ] 317.28K  --.-KB/s    in 0.04s   

2023-05-10 18:18:47 (8.51 MB/s) - ‘7T47.pdb’ saved [324891]



In [124]:
# get ligand
!grep 6IC 7T47.pdb > lig.pdb

In [132]:
# get protein
# !grep ATOM 7T47.pdb > rec.pdb #not as good as the one below

!grep -v 6IC 7T47.pdb > rec.pdb

In [3]:
#prepared protein perform worse than the unmodified protein 8.0 vs. 9.847 (positive control)

In [130]:
# geometry optimization via openbabel
# !obabel rec.pdb -Orec.pdb

In [7]:
#| export
def view_complex(receptor, # protein file
                 ligand, # ligand (green), or docked ligand
                 ori_ligand = None, #original ligand (yellow)
                ):
    v = py3Dmol.view()
    v.addModel(open(receptor).read())
    v.setStyle({'cartoon':{},'stick':{'radius':0.15}})
    
    v.addModel(open(ligand).read())
    v.setStyle({'model':1},
               {'stick':
                {'colorscheme':'greenCarbon'}
               }
              )
    
    if ori_ligand is not None:
    
        v.addModel(open(ori_ligand).read())
        v.setStyle({'model':2},
                   {'stick':
                    {'colorscheme':'yellowCarbon'}
                   })
    
    v.zoomTo({'model':1})
    v.show()

In [8]:
show_doc(view_complex)

---

### view_complex

>      view_complex (receptor, ligand, ori_ligand=None)

|    | **Type** | **Default** | **Details** |
| -- | -------- | ----------- | ----------- |
| receptor |  |  | protein file |
| ligand |  |  | ligand (green), or docked ligand |
| ori_ligand | NoneType | None | original ligand (yellow) |

In [9]:
view_complex('rec.pdb','lig.pdb')

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

### Visualize

In [9]:
#| export
def view_mol(file, #sdf or pdb file
            ):
    v = py3Dmol.view()
    v.addModel(open(file).read())
    v.setStyle({'stick':{}})
    v.zoomTo()
    v.show()

In [10]:
show_doc(view_mol)

---

### view_mol

>      view_mol (file)

|    | **Details** |
| -- | ----------- |
| file | sdf or pdb file |

In [24]:
view_mol('rec.pdb')

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Conformer generation

### Rdkit

In [11]:
import numpy as np

In [6]:
#| export
def rdkit_conformer(SMILES, # SMILES string
                    output, # file ".sdf" to be saved
                    method='ETKDG', # Optimization method, can be 'UFF', 'MMFF' or 'ETKDGv3'
                    visualize=True, #whether or not to visualize the compound
                    seed = 3,# randomness of the 3d
                   ):
    
    np.random.seed(seed) 
    # Generate a 2D molecule from the SMILES string
    mol = Chem.MolFromSmiles(SMILES)
    
    # Generate a 3D conformation of the molecule
    AllChem.EmbedMolecule(mol)
    

    # Optimize the 3D conformation using the specified force field method
    if method == 'UFF':
        AllChem.UFFOptimizeMolecule(mol)
    elif method == 'MMFF':
        AllChem.MMFFOptimizeMolecule(mol)
    elif method == 'ETKDG':
        AllChem.EmbedMultipleConfs(mol, numConfs=1, useExpTorsionAnglePrefs=True, 
                                   useBasicKnowledge=True, enforceChirality=True,randomSeed=seed)
        AllChem.ETKDGv3()
        AllChem.UFFOptimizeMolecule(mol)
        
#     elif method == 'ETKDG_MMFF':
#         AllChem.EmbedMultipleConfs(mol, numConfs=1, useExpTorsionAnglePrefs=True, 
#                                    useBasicKnowledge=True, enforceChirality=True)
#         AllChem.ETKDGv3()
#         AllChem.MMFFOptimizeMolecule(mol)
    else:
        raise ValueError('Invalid method specified')
        

    # Remove hydrogens from the molecule
    # mol = Chem.RemoveHs(mol)
    
    # create the directory if it does not exist
    directory = os.path.dirname(os.path.abspath(output))
    os.makedirs(directory, exist_ok=True)

    # Write the molecule to an SDF file
    w = Chem.SDWriter(output)
    w.write(mol)
    w.close()
    
    if visualize:
        v = py3Dmol.view()
        v.addModel(Chem.MolToMolBlock(mol))
        v.setStyle({'stick':{}})
        v.zoomTo()
        v.show()

In [7]:
show_doc(rdkit_conformer)

---

### rdkit_conformer

>      rdkit_conformer (SMILES, output, method='ETKDG', visualize=True, seed=3)

|    | **Type** | **Default** | **Details** |
| -- | -------- | ----------- | ----------- |
| SMILES |  |  | SMILES string |
| output |  |  | file ".sdf" to be saved |
| method | str | ETKDG | Optimization method, can be 'UFF', 'MMFF' or 'ETKDGv3' |
| visualize | bool | True | whether or not to visualize the compound |
| seed | int | 3 | randomness of the 3d |

In [8]:
#| hide
def extract_values_from_output(output):
    # Search for the line containing mode 1
    mode1_line = re.search(r'\b1\s+(-?\d+\.\d+)\s+(-?\d+\.\d+)\s+(-?\d+\.\d+)\b', output)
    
    if mode1_line:
        # Extract the values from the matched line
        affinity = float(mode1_line.group(1))
        cnn_pose_score = float(mode1_line.group(2))
        cnn_affinity = float(mode1_line.group(3))
        
        return affinity, cnn_pose_score, cnn_affinity
    
    return None

In [9]:
#| export
def gnina(receptor, # receptor file
          ligand, # ligand file
          autobox_ligand, # ligand file isolated from the complex
          output = 'docked.sdf', # output file (sdf or sdf.gz) to be saved
          seed=0, # set seeds
          exhaustiveness=None, # number of MC chains, default is 8 if None, the higher the better (16,32); for whole protein, use 64
         ):
    
    command = ['./gnina', 
               '-r', receptor, 
               '-l', ligand, 
               '--autobox_ligand', autobox_ligand,
               '-o', output,
               '--seed', str(seed)]

    if exhaustiveness is not None:
        command.extend(['--exhaustiveness', str(exhaustiveness)])

    # Run the command and capture the output
    result = subprocess.run(command, capture_output=True, text=True)
    
    print(f'save the docked file as {output}')
    
    values = extract_values_from_output(result.stdout)
    
    
    print(f'affinity, cnn_pose_score, and cnn_affinity are: {values}')

    # Return the command output
    return values

Test the conformer

In [8]:
mrtx = "FC1=C(C2=C(C(C#C)=C(F)C=C3)C3=CC(O)=C2)N=CC4=C1N=C(OC[C@]56N(C[C@H](F)C6)CCC5)N=C4N7C[C@@H](CC8)N[C@@H]8C7"

In [9]:
from tools.dataset import Data

In [11]:
import pandas as pd

In [12]:
df = pd.read_csv('hopping_691.csv')

In [13]:
df

ID                                             SMILES
0       mrtx  C#Cc1c(F)ccc(c12)cc(O)cc2-c(nc3)c(F)c(c34)nc(n...
1      hop_1  C#Cc1c(F)ccc(c12)cc(O)cc2Cc3csc(c34)c(nc([nH+]...
2      hop_2  C1[C@@H](F)CN(CCC2)[C@]12COc3cc(N(C[C@H]45)C[C...
3      hop_3  C1[C@@H](F)CN(CCC2)[C@]12COc(nc3N(C[C@H]45)C[C...
4      hop_4  C1[C@@H](F)CN(CCC2)[C@]12COc3nc(N(C[C@H]45)C[C...
..       ...                                                ...
687  hop_687  C1[C@@H](F)CN(CCC2)[C@]12CO[C@@H](C(=C34)CC(C)...
688  hop_688  C1[C@@H](F)CN(CCC2)[C@]12CO[C@@H]3C(C)(C)[C@@H...
689  hop_689  C1[C@@H](F)CN(CCC2)[C@]12CO[C@@H]3C(C)(C)[C@@H...
690  hop_690  C1[C@@H](F)CN(CCC2)[C@]12CO[C@@H]([C@@](C)(NC3...
691  hop_691  C1[C@@H](F)CN(CCC2)[C@]12COC[C@H]3C(C)(C)[C@@H...

[692 rows x 2 columns]

In [15]:
# use an ensemble of model to make prediction
!./gnina -r rec.pdb -l lig.pdb --autobox_ligand lig.pdb --seed 0 --verbosity 3

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:e9cb230+   Built Feb 11 2023.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Commandline: ./gnina -r rec.pdb -l lig.pdb --autobox_ligand lig.pdb --seed 0 --verbosity 3
*** Open Babel Warning  in Init
  Unable to open data file 'space-groups.txt'
*** Open Babel Warning  in Init
  Cannot initialize database 'space-groups.txt' which may cause further errors.
*** Open Babel Warning  in parseConectRecord
  Problems reading a CONECT record.
  According to the PDB specification,
  columns 7-11 should contain the serial number of an atom.
  No atom was found with this serial number.
  THIS CONECT RECORD WILL BE IGNORED.

*** Open Babel Warning  in parseConectRecord
  Problems reading a CONECT record.
  According to the PDB spec

In [18]:
df = Data.get_g12d_dedup()

In [19]:
df.shape

(660, 5)

In [24]:
df2 = df[400:].copy() #forgot to save 120:240 (:120, 120:240,240:400, 400:)

In [25]:
df2

ID  \
400    US_457   
401    US_458   
402    US_465   
403    US_466   
404    US_469   
..        ...   
655  paper_23   
656  paper_22   
657  paper_35   
658     US_56   
659     US_66   

                                                                                                           SMILES  \
400                               Cc1cc2sc(N)nc2c(c1C)-c1ncc2c(nc(OC[C@@]34CCCN3C[C@H](F)C4)nc2c1F)N1CC2CCC(C1)N2   
401                                             Cc1ccc2sc(N)nc2c1-c1ncc2c(nc(OCC34CCCN3CCC4)nc2c1F)N1CC2CCC(C1)N2   
402          [C@H]12CN(C[C@H](CC1)N2)C=2C1=C(N=C(N2)OC[C@]23CCCN3C[C@@H](C2)F)C(=C(N=C1)C1=CC=CC2=CC=CC(=C12)CC)F   
403     [C@H]12CN(C[C@H](CC1)N2)C3=NC(=NC4=C3C=NC(=C4F)C5=CC=CC6=CC=CC(=C56)CC)OC[C@@]78C[C@@H](CN7C[C@@H](C8)O)O   
404  [C@H]12CN(C[C@H](CC1)N2)C=2C1=C(N=C(N2)OC[C@]23CCCCN3C[C@@H](C2)F)C(=C(N=C1)C1=CC(=CC2=CC=C(C(=C12)C#C)F)O)F   
..                                                                                                            ...   
655                  FC1=C(C2=C(C=CC=C3)C3=CC(O)=C2)N=CC4=C1N=C(OCC56N(CCC6)C(CC5)=O)N=C4N7C[C@@H](CC8)N[C@@H]8C7   
656                     FC1=C(C2=C(C=CC=C3)C3=CC(O)=C2)N=CC4=C1N=C(OCC5(CCCC6)N6CCC5)N=C4N7C[C@@H](CC8)N[C@@H]8C7   
657                   FC1=C(C2=C(C(F)=C(F)C=C3)C3=CC=C2)N=CC4=C1N=C(OCC56N(CCC6)CCC5)N=C4N7C[C@@H](CC8)N[C@@H]8C7   
658                                           OC[C@@H](O)COc1nc(N2CC3CCC(C2)N3)c2cnc(c(F)c2n1)-c1cccc2cccc(Cl)c12   
659                                 Fc1c(ncc2c(nc(OC[C@@]34CCCN3C(CCl)CC4)nc12)N1CC2CCC(C1)N2)-c1cccc2cccc(Cl)c12   

          Kd    IC50  erk_IC50  
400      NaN   475.0       NaN  
401      NaN   143.0       NaN  
402      NaN     1.0       NaN  
403      NaN     6.0       NaN  
404      NaN     2.0      31.6  
..       ...     ...       ...  
655      NaN   750.5   10000.0  
656      NaN    12.0     650.0  
657      NaN     7.0      97.0  
658  13805.3  6024.0       NaN  
659      NaN   273.8    1332.6  

[260 rows x 5 columns]

In [14]:
from tqdm import tqdm

In [17]:
import numpy as np

In [15]:
import seaborn as sns

In [19]:
df2 = df.copy()

In [21]:
df = df2[:450].copy()

In [22]:
df

ID                                             SMILES
0       mrtx  C#Cc1c(F)ccc(c12)cc(O)cc2-c(nc3)c(F)c(c34)nc(n...
1      hop_1  C#Cc1c(F)ccc(c12)cc(O)cc2Cc3csc(c34)c(nc([nH+]...
2      hop_2  C1[C@@H](F)CN(CCC2)[C@]12COc3cc(N(C[C@H]45)C[C...
3      hop_3  C1[C@@H](F)CN(CCC2)[C@]12COc(nc3N(C[C@H]45)C[C...
4      hop_4  C1[C@@H](F)CN(CCC2)[C@]12COc3nc(N(C[C@H]45)C[C...
..       ...                                                ...
445  hop_445  C1[C@@H](F)CN(CCC2)[C@]12CO[C@@H]([C@]3(C)CN(C...
446  hop_446  C1[C@@H](F)CN(CCC2)[C@]12COC(=O)N([C@@H]3C(=O)...
447  hop_447  C1[C@@H](F)CN(CCC2)[C@]12CO[C@@H](C3)C[C@H](C4...
448  hop_448  C1[C@@H](F)CN(CCC2)[C@]12COc3c(F)c(N(C[C@H]45)...
449  hop_449  C#Cc1c(F)ccc(c12)cc(O)cc2[C@H]([C@H](N3)CNS(=O...

[450 rows x 2 columns]

In [ ]:
affinity_values = []
cnn_pose_score_values = []
cnn_affinity_values = []

# Create a tqdm progress bar
progress_bar = tqdm(total=len(df), desc='Processing')

for i, r in df.iterrows():
    rdkit_conformer(r.SMILES, f'ligand/{r.ID}.sdf')
    affinity, cnn_pose_score, cnn_affinity = gnina('rec.pdb',f'ligand/{r.ID}.sdf', 'lig.pdb',f'docked/docked_{r.ID}.sdf')
    
    affinity_values.append(affinity)
    cnn_pose_score_values.append(cnn_pose_score)
    cnn_affinity_values.append(cnn_affinity)
    
    # Update the progress bar
    progress_bar.update(1)
    
# Close the progress bar
progress_bar.close()

# Assign the calculated values as new columns in the DataFrame
df = df.copy()
df['Affinity'] = affinity_values
df['CNN_Pose_Score'] = cnn_pose_score_values
df['CNN_Affinity'] = cnn_affinity_values
df.to_csv('hopping_450.csv',index=False)

Processing:   6%|▌         | 40/692 [27:02<7:20:42, 40.56s/it]
[19:36:33] Molecule does not have explicit Hs. Consider calling AddHs()
[19:36:33] Molecule does not have explicit Hs. Consider calling AddHs()
[19:36:33] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Processing:   0%|          | 1/450 [00:29<3:39:20, 29.31s/it]

save the docked file as docked/docked_mrtx.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.67, 0.7473, 9.381)


[19:37:02] Molecule does not have explicit Hs. Consider calling AddHs()
[19:37:02] Molecule does not have explicit Hs. Consider calling AddHs()
[19:37:02] Molecule does not have explicit Hs. Consider calling AddHs()


...

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Processing:  26%|██▌       | 117/450 [1:16:48<3:37:27, 39.18s/it]

save the docked file as docked/docked_hop_116.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-3.02, 0.5809, 9.359)


[20:53:21] Molecule does not have explicit Hs. Consider calling AddHs()
[20:53:21] Molecule does not have explicit Hs. Consider calling AddHs()
[20:53:22] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [20]:
# randomness!!! everytime is different!!
for seed in [123,2,3]:
    rdkit_conformer(mrtx, f'mrtx_seed{seed}.sdf',seed=seed)
    gnina('rec.pdb',f'mrtx_seed{seed}.sdf', 'lig.pdb',f'docked_seed{seed}.sdf')

[21:29:35] Molecule does not have explicit Hs. Consider calling AddHs()
[21:29:35] Molecule does not have explicit Hs. Consider calling AddHs()
[21:29:35] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

save the docked file as docked_seed123.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-8.98, 0.5917, 8.974)


[21:30:02] Molecule does not have explicit Hs. Consider calling AddHs()
[21:30:02] Molecule does not have explicit Hs. Consider calling AddHs()
[21:30:03] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

save the docked file as docked_seed2.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.43, 0.7272, 9.377)


[21:30:32] Molecule does not have explicit Hs. Consider calling AddHs()
[21:30:32] Molecule does not have explicit Hs. Consider calling AddHs()
[21:30:32] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

save the docked file as docked_seed3.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.69, 0.731, 9.342)


In [104]:
# Generate conformers
for method in ['UFF','MMFF','ETKDGv3']:
    rdkit_conformer(mrtx, f'mrtx_{method}.sdf',method)

[20:13:21] Molecule does not have explicit Hs. Consider calling AddHs()
[20:13:21] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

[20:13:21] Molecule does not have explicit Hs. Consider calling AddHs()
[20:13:21] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

[20:13:21] Molecule does not have explicit Hs. Consider calling AddHs()
[20:13:22] Molecule does not have explicit Hs. Consider calling AddHs()
[20:13:22] Molecule does not have explicit Hs. Consider calling AddHs()


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [144]:
# check which optimization is best
for method in ['ETKDG_UFF','ETKDG_MMFF']:
    gnina('rec.pdb',f'mrtx_{method}.sdf', 'lig.pdb',f'docked_{method}.sdf')

save the docked file as docked_ETKDG_UFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-6.56, 0.6205, 9.008)
save the docked file as docked_ETKDG_MMFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-8.12, 0.4988, 8.949)


In [105]:
# without Hs before geometry optimization
for method in ['UFF','MMFF','ETKDGv3']:
    gnina('rec.pdb',f'mrtx_{method}.sdf', 'lig.pdb',f'docked_{method}.sdf')

save the docked file as docked_UFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.76, 0.6052, 8.001)
save the docked file as docked_MMFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-2.32, 0.5676, 6.6)
save the docked file as docked_ETKDGv3.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.68, 0.6311, 8.038)


In [91]:
# add Hs before geometry optimization
for method in ['UFF','MMFF','ETKDGv3']:
    gnina('rec.pdb',f'mrtx_{method}.sdf', 'lig.pdb',f'docked_{method}.sdf')

save the docked file as docked_UFF.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: (-2.16, 0.6111, 6.742)
save the docked file as docked_MMFF.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: (-3.35, 0.5616, 6.836)
save the docked file as docked_ETKDGv3.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: (-11.61, 0.5937, 7.989)


In [120]:
# complex file only delete the ligand
for method in ['UFF','MMFF','ETKDGv3']:
    gnina('rec_3.pdb',f'mrtx_{method}.sdf', 'lig.pdb',f'docked_{method}.sdf')

save the docked file as docked_UFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.64, 0.7334, 9.351)
save the docked file as docked_MMFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-7.57, 0.5036, 8.922)
save the docked file as docked_ETKDGv3.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.75, 0.7081, 9.319)


In [134]:
# without receptor.pdb optimization via openbabel
for method in ['UFF','MMFF','ETKDGv3']:
    gnina('rec_3.pdb',f'mrtx_{method}.sdf', 'lig.pdb',f'docked_{method}.sdf')

save the docked file as docked_UFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.64, 0.7334, 9.351)
save the docked file as docked_MMFF.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-7.57, 0.5036, 8.922)
save the docked file as docked_ETKDGv3.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-11.75, 0.7081, 9.319)


In [96]:
gnina?

Signature:
gnina(
    receptor,
    ligand,
    autobox_ligand,
    output='docked.sdf',
    seed=0,
    exhaustiveness=None,
)
Docstring: <no docstring>
File:      /tmp/ipykernel_66/1606466012.py
Type:      function


In [97]:
gnina('rec.pdb','lig.pdb','lig.pdb')

save the docked file as docked.sdf
affinity, cnn_pose_score, and cnn_affinity are: (-14.75, 0.9539, 8.551)


(-14.75, 0.9539, 8.551)

In [99]:
view_complex('rec.pdb','docked.sdf','lig.pdb')

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [123]:
view_complex('rec.pdb','docked_MMFF.sdf','lig.pdb')

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [107]:
!obrms lig.pdb docked_UFF.sdf

RMSD lig.pdb: 0.917565


In [108]:
!obrms lig.pdb docked_ETKDGv3.sdf

RMSD lig.pdb: 0.902488


According to the results
1) we should not add Hs to the compound before geometry optimization
2) withou Hs added, UFF and ETKDGv3 perform relatively similar. UFF performs slightly better in temrs of rmsd
3) there's some randomness when generating the 3d molecules using rdkit

### Uni-mol conformer

In [230]:
!wget https://unimol.dp.tech/data/finetune/conformation_generation.tar.gz --no-check-certificate

--2023-05-12 01:52:22--  https://unimol.dp.tech/data/finetune/conformation_generation.tar.gz
Resolving unimol.dp.tech (unimol.dp.tech)... 39.98.20.35
Connecting to unimol.dp.tech (unimol.dp.tech)|39.98.20.35|:443... connected.
	requested host name ‘unimol.dp.tech’.
HTTP request sent, awaiting response... 403 Forbidden
2023-05-12 01:52:24 ERROR 403: Forbidden.



In [ ]:
!git clone https://gist.github.com/ZhouGengmo/5b565f51adafcd911c0bc115b2ef027c

In [37]:
show_doc(smi2sdf)

---

### smi2sdf

>      smi2sdf (SMILES, output, method='UFF', visualize=True)

|    | **Type** | **Default** | **Details** |
| -- | -------- | ----------- | ----------- |
| SMILES |  |  | SMILES string |
| output |  |  | file ".sdf" to be saved |
| method | str | UFF | Optimization method, can be 'UFF', 'MMFF' or 'ETKDGv3' |
| visualize | bool | True | whether or not to visualize the compound |

In [ ]:
smi2sdf('')

In [227]:
gnina('rec.pdb','G12C.sdf','lig.pdb')

save the docked file as docked.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-3.52, 0.4551, 6.206), b'RMSD : 40.3436\nRMSD : 39.7777\nRMSD : 39.8234\nRMSD : 40.1\nRMSD : 39.4353\nRMSD : 38.4855\nRMSD : 40.411\nRMSD : 34.2085\nRMSD : 37.5771\n')


((-3.52, 0.4551, 6.206),
 b'RMSD : 40.3436\nRMSD : 39.7777\nRMSD : 39.8234\nRMSD : 40.1\nRMSD : 39.4353\nRMSD : 38.4855\nRMSD : 40.411\nRMSD : 34.2085\nRMSD : 37.5771\n')

In [220]:
gnina?

Signature:
gnina(
    receptor,
    ligand,
    autobox_ligand,
    output='docked.sdf',
    seed=0,
    exhaustiveness=None,
)
Docstring: <no docstring>
File:      /tmp/ipykernel_108/861585805.py
Type:      function


In [224]:
gnina('rec.pdb','G12D_5A.sdf','lig.pdb','docked_G12D_9.sdf')

save the docked file as docked_G12D_9.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-7.02, 0.5931, 7.484), b'RMSD : 33.4037\nRMSD : 33.9729\nRMSD : 39.9215\nRMSD : 32.9629\nRMSD : 38.6188\nRMSD : 33.9926\nRMSD : 33.4473\nRMSD : 38.3724\nRMSD : 39.5488\n')


((-7.02, 0.5931, 7.484),
 b'RMSD : 33.4037\nRMSD : 33.9729\nRMSD : 39.9215\nRMSD : 32.9629\nRMSD : 38.6188\nRMSD : 33.9926\nRMSD : 33.4473\nRMSD : 38.3724\nRMSD : 39.5488\n')

In [221]:
gnina('rec.pdb','G12D_9.sdf','lig.pdb','docked_G12D_9.sdf')

save the docked file as docked_G12D_9.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-11.24, 0.5971, 7.275), b'RMSD : 32.9966\nRMSD : 37.7925\nRMSD : 38.1915\nRMSD : 33.5697\nRMSD : 33.208\nRMSD : 33.8665\nRMSD : 32.8998\nRMSD : 37.1789\nRMSD : 34.2615\n')


((-11.24, 0.5971, 7.275),
 b'RMSD : 32.9966\nRMSD : 37.7925\nRMSD : 38.1915\nRMSD : 33.5697\nRMSD : 33.208\nRMSD : 33.8665\nRMSD : 32.8998\nRMSD : 37.1789\nRMSD : 34.2615\n')

In [39]:
MRTX1133 = "FC1=C(C2=C(C(C#C)=C(F)C=C3)C3=CC(O)=C2)N=CC4=C1N=C(OC[C@]56N(C[C@H](F)C6)CCC5)N=C4N7C[C@@H](CC8)N[C@@H]8C7"

In [184]:
!obrms data/mrtx.sdf data/UFF.sdf

RMSD 162369732: 9.15316


In [203]:
!obrms data/UFF.sdf data/UFF.sdf

RMSD : 0


In [212]:
!obrms -f lig.pdb docked.sdf

RMSD lig.pdb: 0.399654
RMSD lig.pdb: 1.65256
RMSD lig.pdb: 11.7981
RMSD lig.pdb: 11.8459
RMSD lig.pdb: 11.3802
RMSD lig.pdb: 2.60489
RMSD lig.pdb: 11.3525
RMSD lig.pdb: 9.17148
RMSD lig.pdb: 10.3674


## Docking via gnina

In [90]:
show_doc(gnina)

---

### gnina

>      gnina (receptor, ligand, autobox_ligand, output='docked.sdf', seed=0,
>             exhaustiveness=None)

|    | **Type** | **Default** | **Details** |
| -- | -------- | ----------- | ----------- |
| receptor |  |  | receptor file |
| ligand |  |  | ligand file |
| autobox_ligand |  |  | ligand file isolated from the complex |
| output | str | docked.sdf | output file (sdf or sdf.gz) to be saved |
| seed | int | 0 | set seeds |
| exhaustiveness | NoneType | None | number of MC chains, default is 8 if None, the higher the better (16,32); for whole protein, use 64 |

In [102]:
gnina('rec.pdb','data/MMFF.sdf','lig.pdb')
gnina('rec.pdb','data/ETK.sdf','lig.pdb')
gnina('rec.pdb','data/UFF.sdf','lig.pdb')

save the docked file as docked.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-10.76, 0.5617, 7.967), 36.5818)
save the docked file as docked.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-11.79, 0.6337, 8.036), 35.1219)
save the docked file as docked.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-10.63, 0.5704, 7.957), 38.4936)


((-10.63, 0.5704, 7.957), 38.4936)

In [105]:
gnina('rec.pdb','lig.pdb','lig.pdb')

save the docked file as docked.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-14.75, 0.9539, 8.551), 10.3674)


((-14.75, 0.9539, 8.551), 10.3674)

In [110]:
rmsd('lig.pdb','docked.sdf')

0.399654

In [214]:
gnina('rec.pdb','data/ETK.sdf','lig.pdb')

save the docked file as docked.sdf
affinity, cnn_pose_score, cnn_affinity, and rmsd to original are: ((-11.79, 0.6337, 8.036), b'RMSD : 33.1702\nRMSD : 33.4502\nRMSD : 38.0734\nRMSD : 37.5708\nRMSD : 33.46\nRMSD : 33.3803\nRMSD : 38.3974\nRMSD : 37.1111\nRMSD : 35.1219\n')


((-11.79, 0.6337, 8.036),
 b'RMSD : 33.1702\nRMSD : 33.4502\nRMSD : 38.0734\nRMSD : 37.5708\nRMSD : 33.46\nRMSD : 33.3803\nRMSD : 38.3974\nRMSD : 37.1111\nRMSD : 35.1219\n')

In [88]:
a = gnina('rec.pdb','lig.pdb','lig.pdb')

In [92]:
extract_values_from_output(a)

(-14.75, 0.9539, 8.551)

In [93]:
rmsd('','')

Signature: rmsd(file1, file2)
Docstring: <no docstring>
Source:   
def rmsd(file1, file2):
    # Run the obrms command and capture its output
    output = subprocess.check_output(["obrms", file1, file2])
    
    # Decode the output from bytes to string
    output_str = output.decode('utf-8')
    
    # Extract the RMSD value from the output string
    rmsd_value = float(output_str.split()[-1])
    
    
    return rmsd_value
File:      /tmp/ipykernel_108/2465251846.py
Type:      function


In [53]:
!./gnina -r rec.pdb -l l4.sdf --autobox_ligand lig.pdb --seed 0 -o ksks.sdf --minimize

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:e9cb230+   Built Feb 11 2023.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Commandline: ./gnina -r rec.pdb -l l4.sdf --autobox_ligand lig.pdb --seed 0 -o ksks.sdf --minimize
Affinity: -3.80931  -1.50151 (kcal/mol)
RMSD: 3.45165
CNNscore: 0.19789 
CNNaffinity: 6.09626
CNNvariance: 0.01034


In [59]:
!./gnina -r rec.pdb -l lig.pdb --autobox_ligand lig.pdb --seed 0

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:e9cb230+   Built Feb 11 2023.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Commandline: ./gnina -r rec.pdb -l lig.pdb --autobox_ligand lig.pdb --seed 0
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | initial pose not within box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | i

In [81]:
!./gnina -r rec.pdb -l data/UFF.sdf --autobox_ligand lig.pdb --seed 0 -o ksks4.sdf --cnn_scoring refinement

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:e9cb230+   Built Feb 11 2023.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Commandline: ./gnina -r rec.pdb -l data/UFF.sdf --autobox_ligand lig.pdb --seed 0 -o ksks4.sdf
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
 | pose 0 | initial pose not within box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box

mode |  affinity  |    CNN     |   CNN
     | (kcal/mol) | pose score | affinity
-----+------------+------------+----------
    1      -10.63       0.5704      7.957
    2       -2.29       0.5426      6.346
   

In [84]:
!./gnina -r rec.pdb -l data/ETK.sdf --autobox_ligand lig.pdb --seed 0 -o ksks4.sdf

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:e9cb230+   Built Feb 11 2023.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Commandline: ./gnina -r rec.pdb -l data/ETK.sdf --autobox_ligand lig.pdb --seed 0 -o ksks4.sdf
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
 | pose 0 | initial pose not within box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | initial pose not within box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box
 | pose 0 | ligand outside box

mode |  affinity

In [60]:
view_complex??

Signature: view_complex(receptor, ligand)
Docstring: <no docstring>
Source:   
def view_complex(receptor, # protein file
                 ligand, # compound file
                ):
    v = py3Dmol.view()
    v.addModel(open('rec.pdb').read())
    v.setStyle({'cartoon':{},'stick':{'radius':0.15}})
    v.addModel(open('lig.pdb').read())
    v.setStyle({'model':1},
               {'stick':
                {'colorscheme':'greenCarbon'}
               }
              )
    v.zoomTo({'model':1})
    v.show()
File:      /tmp/ipykernel_108/1319219108.py
Type:      function


In [44]:
!gunzip docked.sdf.gz

gzip: docked.sdf already exists; do you wish to overwrite (y or n)? ^C


In [112]:
!obrms -f lig.pdb docked.sdf

RMSD lig.pdb: 0.399654
RMSD lig.pdb: 1.65256
RMSD lig.pdb: 11.7981
RMSD lig.pdb: 11.8459
RMSD lig.pdb: 11.3802
RMSD lig.pdb: 2.60489
RMSD lig.pdb: 11.3525
RMSD lig.pdb: 9.17148
RMSD lig.pdb: 10.3674


In [137]:
!obrms lig.pdb lig.pdb

RMSD lig.pdb:lig.pdb 0


In [153]:
match = re.search(r"\d+(?:\.\d+)?", "RMSD lig.pdb:lig.pdb 0.3838")
print(match.group())

0.3838


In [147]:
match.group()

'0.29292'

In [177]:
rmsd('docked.sdf','docked.sdf')

0.0

In [117]:
rmsd??

Signature: rmsd(file1, file2)
Docstring: <no docstring>
Source:   
def rmsd(file1, file2):
    # Run the obrms command and capture its output
    output = subprocess.check_output(["obrms", file1, file2])
    
    # Decode the output from bytes to string
    output_str = output.decode('utf-8')
    
    # Extract the RMSD value from the output string
    rmsd_value = float(output_str.split()[-1])
    
    
    return rmsd_value
File:      /tmp/ipykernel_108/2465251846.py
Type:      function


In [116]:
rmsd('lig.pdb','docked.sdf',)

0.399654

In [111]:
!obrms

obrms: Computes the heavy-atom RMSD of identical compound structures.
Usage: obrms reference_file [test_file]
Options:
	 -o, --out        re-oriented test structure output
	 -f, --firstonly  use only the first structure in the reference file
	 -m, --minimize   compute minimum RMSD
	 -x, --cross      compute all n^2 RMSDs between molecules of reference file
	 -s, --separate   separate reference file into constituent molecules and report best RMSD
	 -h, --help       help message
Command line parse error: test file is required but missing


In [99]:
import gzip
v = py3Dmol.view()
v.addModel(open('rec.pdb').read())
v.setStyle({'cartoon':{},'stick':{'radius':.1}})

v.addModel(open('lig.pdb').read())
v.setStyle({'model':1},{'stick':{'colorscheme':'dimgrayCarbon','radius':.125}})

v.addModelsAsFrames(open('docked.sdf','rt').read())
v.setStyle({'model':2},{'stick':{'colorscheme':'greenCarbon'}})

# v.animate({'interval':1000})

v.zoomTo({'model':1})
v.rotate(90)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
v = py3Dmol.view()
v.addModel(open('lig.pdb').read())
v.setStyle({'stick':{'colorscheme':'greenCarbon'}})
v.zoomTo()

In [5]:
#| hide
import sys
sys.path.append("/notebooks/tools")
from nbdev.showdoc import *
%matplotlib inline

In [6]:
#| export
from tools.dataset import Data
from fastbook import *
from rdkit import Chem
from rdkit.Chem import AllChem, DataStructs

In [5]:
show_doc(tanimoto)

---

[source](https://github.com/sky1ove/tools/blob/main/tools/toolbox.py#L13){target="_blank" style="float:right; font-size:smaller"}

### tanimoto

>      tanimoto (df, smiles_col='SMILES', id_col='ID', target_col=None,
>                radius=2)

Calculates the Tanimoto similarity scores between all pairs of molecules in a pandas DataFrame.

|    | **Type** | **Default** | **Details** |
| -- | -------- | ----------- | ----------- |
| df |  |  | pandas DataFrame with SMILES and ID columns. |
| smiles_col | str | SMILES | name of the column containing the SMILES strings (default: 'SMILES'). |
| id_col | str | ID | name of the column containing the molecule IDs (default: 'ID'). |
| target_col | NoneType | None | name of the column containing the target values (default: None). |
| radius | int | 2 | radius of the Morgan fingerprint (default: 2). |

In [8]:
#| hide
import nbdev; nbdev.nbdev_export()